In [1]:
import numpy as np
from TMDP import TMDP
from River_swim import River

from algorithms import *
from model_functions import *

import matplotlib.pyplot as plt
import gymnasium as gym
from FrozenLake import *

#np.set_printoptions(precision=4)
import math
from utils import *

import torch
import torch.nn as nn
from torch.nn import functional as F


nrows = 30
nS = nrows**2
nA = 4
seed = get_current_seed()
gamma = .9
tau = 1.
#tmdp = TMDP(river, xi, tau=tau, gamma=gamma, seed=seed)
#mdp = TMDP(river, xi, tau=0., gamma=gamma, seed=seed)

env = FrozenLakeEnv(is_slippery=False, seed=seed, desc=generate_random_map(nrows))#, render_mode="human")
xi_frozen = np.ones(env.nS) * 1/env.nS

Current seed for result reproducibility: 94019492770581671907432202825143583240


In [2]:
tmdp = TMDP(env, xi_frozen, tau=tau, gamma=gamma, seed=seed)

In [3]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

In [4]:
q_c = np.zeros((nS, nA))
tmdp.update_tau(.8)
cur_res = curriculum_AC(tmdp, q_c, alpha = 0.2, alpha_pol = 0.1, episodes=1000000, 
                        batch_nS=4, temperature=6., biased=False, lam=0., 
                        epochs=1, use_delta_Q=False, final_temperature=1e-6)


No valid pairs found
[(0.0, 0.8)]
Alpha*: 0.0 tau*: 0.8 Episode: 24 length: 6 #teleports:18
Time for bound evaluation:  0.17418432235717773
No valid pairs found
[(0.0, 0.8)]
Alpha*: 0.0 tau*: 0.8 Episode: 38 length: 4 #teleports:10
Time for bound evaluation:  0.10018086433410645
No valid pairs found
[(0.0, 0.8)]
Alpha*: 0.0 tau*: 0.8 Episode: 59 length: 4 #teleports:17
Time for bound evaluation:  0.048009395599365234
No valid pairs found
[(0.0, 0.8)]
Alpha*: 0.0 tau*: 0.8 Episode: 85 length: 4 #teleports:22
Time for bound evaluation:  0.049010276794433594
No valid pairs found
[(0.0, 0.8)]
Alpha*: 0.0 tau*: 0.8 Episode: 128 length: 5 #teleports:38
Time for bound evaluation:  0.05001068115234375
No valid pairs found
[(0.0, 0.8)]
Alpha*: 0.0 tau*: 0.8 Episode: 163 length: 5 #teleports:30
Time for bound evaluation:  0.05001068115234375
No valid pairs found
[(0.0, 0.8)]
Alpha*: 0.0 tau*: 0.8 Episode: 205 length: 4 #teleports:38
Time for bound evaluation:  0.04800987243652344
No valid pairs 

In [5]:
print(cur_res["Qs"][-1])
Q = cur_res["Qs"][-1]
print(get_policy(get_softmax_policy(cur_res["thetas"][-1])))

[[3.91770437e-45 1.01776856e-45 7.74285713e-45 4.17805116e-45]
 [4.14639541e-45 0.00000000e+00 2.19931613e-44 1.09373347e-44]
 [7.25653176e-45 2.82575364e-44 3.98468059e-44 2.56567043e-44]
 ...
 [5.82414234e-02 1.14634346e-01 3.52888139e-01 1.03697027e-01]
 [1.35628008e-01 2.61888262e-01 9.99994984e-01 2.11804928e-01]
 [0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00]]
[[1. 0. 0. 0.]
 [1. 0. 0. 0.]
 [1. 0. 0. 0.]
 ...
 [0. 0. 1. 0.]
 [0. 0. 1. 0.]
 [1. 0. 0. 0.]]


In [6]:
from utils import *
res = {"Q":cur_res["Qs"][-1], "theta":cur_res["thetas"][-1]}
json_res = to_json(res, indent=True)
write_results(nrows, nA, "FrozenLake", json_res, "w")


In [7]:
json_res = read_results(nrows, nA, "FrozenLake")
res = from_json(json_res)
pi = get_softmax_policy(np.array(res["theta"]))
Q = np.array(res["Q"])

In [13]:
print(q_c)
pi= get_policy(q_c)

[[3.91770437e-45 1.01776856e-45 7.74285713e-45 4.17805116e-45]
 [4.14639541e-45 0.00000000e+00 2.19931613e-44 1.09373347e-44]
 [7.25653176e-45 2.82575364e-44 3.98468059e-44 2.56567043e-44]
 ...
 [5.82414234e-02 1.14634346e-01 3.52888139e-01 1.03697027e-01]
 [1.35628008e-01 2.61888262e-01 9.99994984e-01 2.11804928e-01]
 [0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00]]


In [12]:
pi = get_policy(get_softmax_policy(cur_res["thetas"][-1]))
print(pi)

[[1. 0. 0. 0.]
 [1. 0. 0. 0.]
 [1. 0. 0. 0.]
 ...
 [0. 0. 1. 0.]
 [0. 0. 1. 0.]
 [1. 0. 0. 0.]]


In [15]:
tmdp.update_tau(0.)
tmdp.reset()
done = False
step = 0
env.render_mode = "human"
while True:
    s = tmdp.env.s
    a = greedy(tmdp.env.s, pi, tmdp.env.allowed_actions[int(tmdp.env.s)])
    s_prime, reward, flags, prob = tmdp.step(a)
    print("state {} action {} next state {} reward {}".format(s, a, s_prime, reward))
    if flags["done"]:
        tmdp.reset()
    step +=1
    if step > max(100,nrows*2):
        break


state 0 action 2 next state 1 reward 0.0
state 1 action 2 next state 2 reward 0.0
state 2 action 2 next state 3 reward 0.0
state 3 action 2 next state 4 reward 0.0
state 4 action 2 next state 5 reward 0.0
state 5 action 1 next state 35 reward 0.0
state 35 action 1 next state 65 reward 0.0
state 65 action 2 next state 66 reward 0.0
state 66 action 1 next state 96 reward 0.0
state 96 action 2 next state 97 reward 0.0
state 97 action 1 next state 127 reward 0.0
state 127 action 2 next state 128 reward 0.0
state 128 action 2 next state 129 reward 0.0
state 129 action 1 next state 159 reward 0.0
state 159 action 2 next state 160 reward 0.0
state 160 action 2 next state 161 reward 0.0
state 161 action 1 next state 191 reward 0.0
state 191 action 2 next state 192 reward 0.0
state 192 action 2 next state 193 reward 0.0
state 193 action 2 next state 194 reward 0.0
state 194 action 1 next state 224 reward 0.0
state 224 action 2 next state 225 reward 0.0
state 225 action 2 next state 226 reward 0